# **mp3 preprocess**

In [0]:
#@title import libraries
# !pip install librosa
import librosa
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import librosa.display
import IPython.display as ipd
%matplotlib inline
import os
from PIL import Image
import pathlib
import csv

# Preprocessing
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler

# import warnings
# warnings.filterwarnings('ignore')

import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable
from torch.utils.data import DataLoader

In [0]:
#@title load files
#####
from google.colab import files
uploaded = files.upload()
#####

Saving result_v1_simple_gan.wav to result_v1_simple_gan.wav


In [0]:
#@title preprocess MP3/wav
y, sr = librosa.load('music.wav', mono=True,duration = 10)
chroma_stft = librosa.feature.chroma_stft(y=y, sr=sr)         #Chroma Frequencies
spec_cent = librosa.feature.spectral_centroid(y=y, sr=sr)     #Spectral Centroid,
spec_bw = librosa.feature.spectral_bandwidth(y=y, sr=sr)      #spectral_bandwidth
rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr)        #Spectral Roll-off
zcr = librosa.feature.zero_crossing_rate(y)                   #Zero Crossing Rate
mfcc = librosa.feature.mfcc(y=y, sr=sr)                       #Mel-frequency cepstral coefficients
music = np.vstack((chroma_stft,spec_cent,spec_bw,rolloff,zcr,mfcc))

yc, src = librosa.load('BGM.wav', mono=True,duration = 10)
cchroma_stft = librosa.feature.chroma_stft(y=yc, sr=src)         #Chroma Frequencies
cspec_cent = librosa.feature.spectral_centroid(y=yc, sr=src)     #Spectral Centroid,
cspec_bw = librosa.feature.spectral_bandwidth(y=yc, sr=src)      #spectral_bandwidth
crolloff = librosa.feature.spectral_rolloff(y=yc, sr=src)        #Spectral Roll-off
czcr = librosa.feature.zero_crossing_rate(yc)                   #Zero Crossing Rate
cmfcc = librosa.feature.mfcc(y=yc, sr=src)                       #Mel-frequency cepstral coefficients
accompliant = np.vstack((cchroma_stft,cspec_cent,cspec_bw,crolloff,czcr,cmfcc))

In [0]:
#@title data checking
#####
print(sr)
print(y)
print(len(mfcc))
#####

22050
[0.31490368 0.56490433 0.5486097  ... 0.46305555 0.46013013 0.40922236]
20


In [0]:
#@title test librosa(unnecessary)
#####
librosa.display.waveplot(y, sr=sr)
ipd.Audio('1.mp3')
#####

#@title
#####
librosa.display.waveplot(yc, sr=src)
ipd.Audio('1c.mp3')
#####

#@title
#####
Y = librosa.stft(y)
Ydb = librosa.amplitude_to_db(abs(Y))
plt.figure(figsize=(14, 5))
librosa.display.specshow(Ydb, sr=sr, x_axis='time', y_axis='hz')
plt.colorbar()
#####

#@title
#####
# write wav file using y and sr
librosa.output.write_wav('test.wav',y,sr)
ipd.Audio('test.wav')
#####

# **simple GAN**

In [0]:
#@title train simple gan
g_sample = np.array(yc)
d_sample = np.array(y)

# https://www.pytorchtutorial.com/4-6-gan-generative-adversarial-nets/

# Hyper Parameters
BATCH_SIZE = 64
LR_G = 0.001           # learning rate for generator#
LR_D = 0.001           # learning rate for discriminator
g_input_size = len(yc)             # think of this as number of ideas for generating an art work (Generator)
g_output_size = len(yc)     # it could be total point G can draw in the canvas
d_input_size = len(y) 
d_output_size = len(y)
num_epochs = 500
d_steps = 10
g_steps = 10

# G and D input
g_sample = Variable(torch.tensor(g_sample)).cuda()
d_sample = Variable(torch.tensor(d_sample)).cuda()

# structure
G = nn.Sequential(                      # Generator
    nn.Linear(g_input_size, 100),            # random ideas (could from normal distribution)
    nn.ReLU(),
    nn.Linear(100, g_output_size),     # making a painting from these random ideas
    nn.Tanh()
).cuda()

D = nn.Sequential(                      # Discriminator
    nn.Linear(d_input_size, 100),     # receive art work either from the famous artist or a newbie like G
    nn.ReLU(),
    nn.Linear(100, d_output_size),
    nn.Sigmoid()                       # tell the probability that the art work is made by artist
).cuda()

opt_D = torch.optim.Adam(D.parameters(), lr=LR_D)
opt_G = torch.optim.Adam(G.parameters(), lr=LR_G)
adversarial_loss = torch.nn.BCELoss()

results = []
for epoch in range(num_epochs):
   
    G_fake = G(g_sample)
    D_real = D(d_sample)
    D_fake = D(G_fake)

    D_loss = - torch.mean(torch.log(D_real) + torch.log(1. - D_fake))
    G_loss = torch.mean(torch.log(1. - D_fake))

    opt_D.zero_grad()
    D_loss.backward(retain_graph=True)
    opt_D.step()

    opt_G.zero_grad()
    G_loss.backward()
    opt_G.step()
    
#     if (epoch+1)%100==0:
#       results.append(G(g_sample).cpu().data.numpy())

In [0]:
#@title show results
print(D_real)
print(D_fake)
print(G_fake)
print(D_loss)
print(G_loss)
# print(len(results))

# for i in range(int(num_epochs/100)):
#   librosa.output.write_wav('result_v2_'+str(i+1)+'.wav',results[i],src)
# ipd.Audio('result_v2_'+str(5)+'.wav')
# print(results[4])
librosa.output.write_wav('result_v1.wav',G(g_sample).cpu().data.numpy(),src)
ipd.Audio('result_v1.wav')

tensor([0.6308, 0.6264, 0.6169,  ..., 0.6063, 0.6291, 0.6107], device='cuda:0',
       grad_fn=<SigmoidBackward>)
tensor([3.7064e-09, 2.4224e-06, 7.1827e-06,  ..., 5.6036e-05, 1.0768e-07,
        6.4268e-05], device='cuda:0', grad_fn=<SigmoidBackward>)
tensor([ 0.0299,  0.0003,  0.0459,  ..., -0.0144, -0.0478,  0.0140],
       device='cuda:0', grad_fn=<TanhBackward>)
tensor(0.4817, device='cuda:0', grad_fn=<NegBackward>)
tensor(-1.6795e-05, device='cuda:0', grad_fn=<MeanBackward1>)


# ** modified simple GAN**

In [0]:
#@title train simple gan
g_sample = np.array(yc)
d_sample = np.array(y)

# https://www.pytorchtutorial.com/4-6-gan-generative-adversarial-nets/

# Hyper Parameters
BATCH_SIZE = 64
LR_G = 0.001           # learning rate for generator#
LR_D = 0.001           # learning rate for discriminator
g_input_size = len(yc)             # think of this as number of ideas for generating an art work (Generator)
g_output_size = len(yc)     # it could be total point G can draw in the canvas
d_input_size = len(y) 
d_output_size = len(y)
num_epochs = 500
d_steps = 1
g_steps = 1

# G and D input
g_sample = Variable(torch.tensor(g_sample)).cuda()
d_sample = Variable(torch.tensor(d_sample)).cuda()

# structure
G = nn.Sequential(                      # Generator
    nn.Linear(g_input_size, 128),            # random ideas (could from normal distribution)
    nn.ReLU(),
    nn.Linear(128, g_output_size),     # making a painting from these random ideas
    nn.Tanh()
).cuda()

D = nn.Sequential(                      # Discriminator
    nn.Linear(d_input_size, 128),     # receive art work either from the famous artist or a newbie like G
    nn.ReLU(),
    nn.Linear(128, d_output_size),
    nn.Sigmoid()                       # tell the probability that the art work is made by artist
).cuda()

opt_D = torch.optim.Adam(D.parameters(), lr=LR_D)
opt_G = torch.optim.Adam(G.parameters(), lr=LR_G)
adversarial_loss = torch.nn.BCELoss()

results = []
for epoch in range(num_epochs):
#     for d_index in range(d_steps):
#         # 1. Train D on real+fake
#         opt_D.zero_grad()

#         #  1A: Train D on real
#         D_real = D(d_sample)
#         #  1B: Train D on fake
#         G_fake = G(g_sample)
#         D_fake = D(G_fake)
#         D_loss = - torch.mean(torch.log(D_real) + torch.log(1. - D_fake)) 
#         D_loss.backward(retain_graph=True) # compute/store gradients
#         opt_D.step() # Only optimizes D's parameters; changes based on stored gradients from backward()

#     for g_index in range(g_steps):
#         # 2. Train G on D's response (but DO NOT train D on these labels)
#         opt_G.zero_grad()

#         G_fake = G(g_sample)
#         D_fake = D(G_fake)
#         G_loss = torch.mean(torch.log(1. - D_fake)) # Train G to pretend it's genuine

#         G_loss.backward()
#         opt_G.step() # Only optimizes G's parameters
    
    G_fake = G(g_sample)
    D_real = D(d_sample)
    D_fake = D(G_fake)

    D_loss = - torch.mean(torch.log(D_real) + torch.log(1. - D_fake))
    G_loss = torch.mean(torch.log(1. - D_fake))

    opt_D.zero_grad()
    D_loss.backward(retain_graph=True)
    opt_D.step()

    opt_G.zero_grad()
    G_loss.backward()
    opt_G.step()
    
#     if (epoch+1)%100==0:
#       results.append(G(g_sample).cpu().data.numpy())

In [0]:
#@title show results
print(D_real)
print(D_fake)
print(G_fake)
print(D_loss)
print(G_loss)
# print(len(results))

# for i in range(int(num_epochs/100)):
#   librosa.output.write_wav('result_v2_'+str(i+1)+'.wav',results[i],src)
# ipd.Audio('result_v2_'+str(5)+'.wav')
# print(results[4])
librosa.output.write_wav('result_v2.wav',G(g_sample).cpu().data.numpy(),src)
ipd.Audio('result_v2.wav')

tensor([0.6116, 0.6212, 0.6076,  ..., 0.6245, 0.6295, 0.6282], device='cuda:0',
       grad_fn=<SigmoidBackward>)
tensor([7.7386e-05, 1.4438e-08, 1.5799e-07,  ..., 3.8569e-07, 1.4088e-10,
        5.4090e-11], device='cuda:0', grad_fn=<SigmoidBackward>)
tensor([-0.0330, -0.0367, -0.0923,  ...,  0.0059, -0.0249, -0.0720],
       device='cuda:0', grad_fn=<TanhBackward>)
tensor(0.4843, device='cuda:0', grad_fn=<NegBackward>)
tensor(-1.0593e-05, device='cuda:0', grad_fn=<MeanBackward1>)


In [0]:
#@title print generative model
# Print model's state_dict
print("Model's state_dict:")
for param_tensor in G.state_dict():
    print(param_tensor, "\t", G.state_dict()[param_tensor].size())

# Print optimizer's state_dict
print("Optimizer's state_dict:")
for var_name in opt_G.state_dict():
    print(var_name, "\t", opt_G.state_dict()[var_name])

In [0]:
#@title save G
# save
torch.save(G.state_dict(), "G.pt")

In [0]:
#@title load G
# load
model = nn.Sequential(                      # Generator
    nn.Linear(g_input_size, 128),            # random ideas (could from normal distribution)
    nn.ReLU(),
    nn.Linear(128, g_output_size),     # making a painting from these random ideas
    nn.Tanh()
).cuda()
model.load_state_dict(torch.load("G.pt"))
# model.eval()

In [0]:
#@title test on other samples
y1, sr1 = librosa.load('Money.mp3', mono=True,duration = 10)
test1_sample = np.array(y1)
test1_sample = Variable(torch.tensor(test1_sample)).cuda()
librosa.output.write_wav('result_v2.wav',model(test1_sample).cpu().data.numpy(),sr1)
ipd.Audio('result_v2.wav')

# **RNN GAN**

In [0]:
#@title preprocess
### y
### preprocess for RNN #1
time_steps = 500
music_length = len(y)
sequence_size = int(music_length/time_steps)

g_sample = np.zeros((sequence_size,time_steps))
d_sample = np.zeros((sequence_size,time_steps))
for i in range(sequence_size):
  g_sample[i] = yc[time_steps*i:time_steps*(i+1)]
  d_sample[i] = y[time_steps*i:time_steps*(i+1)]
  
g_sample = g_sample.reshape(sequence_size,time_steps,1)
d_sample = d_sample.reshape(sequence_size,time_steps,1)

d_sample = Variable(torch.Tensor(d_sample)).cuda()
g_sample = Variable(torch.Tensor(g_sample)).cuda()

# print(d_sample[0:5,0,0])
# print(d_sample)
# print(g_sample)

In [0]:
#@title mfcc(unnecessary)
### mfcc
# x_train_feature = music.T[:-1]
# y_train_feature = y[:x_train_feature.shape[0]*512]


# x_train_feature.shape,y_train_feature.shape

In [0]:
#@title train the models
# https://github.com/devnag/pytorch-generative-adversarial-networks/blob/master/gan_pytorch.py

# ##### DATA: Target data and generator input data

# d_sample = torch.Tensor(d_sample)
# g_sample = torch.Tensor(g_sample)

# ##### MODELS: Generator model and discriminator model

class Generator(nn.Module):
    def __init__(self, input_size, hidden_size, n_layer, output_size):
        super(Generator, self).__init__()
        self.map1 = nn.LSTM(input_size,hidden_size,n_layer,batch_first=True)
        # self.lstm = nn.LSTM(in_dim, hidden_dim, n_layer, batch_first=True)
        self.map2 = nn.Sequential(nn.Linear(hidden_size,hidden_size),
                                 nn.LeakyReLU(),
#                                  nn.Linear(hidden_size,hidden_size),
#                                  nn.Tanh(),
                                 nn.Linear(hidden_size,output_size),
                                 nn.Tanh())
#         self.f = f

    def forward(self, x):
        x,_ = self.map1(x)
#         x = self.f(x)
        x = self.map2(x)
#         x = self.f(x)
#         x = self.map3(x)
        return x

class Discriminator(nn.Module):
    def __init__(self, input_size, hidden_size, n_layer, output_size):
        super(Discriminator, self).__init__()
        self.map1 = nn.LSTM(input_size,hidden_size,n_layer,batch_first=True)
        # self.lstm = nn.LSTM(in_dim, hidden_dim, n_layer, batch_first=True)
        self.map2 = nn.Sequential(nn.Linear(hidden_size,hidden_size),
                                nn.LeakyReLU(),
#                                 nn.Linear(hidden_size,hidden_size),
#                                 nn.Sigmoid(),
                                nn.Linear(hidden_size,output_size),
                                nn.Sigmoid())
#         self.f = f

    def forward(self, x):
#         x = self.f(self.map1(x))
#         x = self.f(self.map2(x))
#         x = self.f(self.map3(x))
        x,_ = self.map1(x)
        x = self.map2(x)
#         x = self.map3(x)
        return x

# Model parameters
g_input_size =  g_sample.size(-1)     # Random noise dimension coming into generator, per output vector
g_hidden_size = 20     # Generator complexity
g_output_size = g_sample.size(-1)     # Size of generated output vector
g_n_layer = 2
d_input_size = d_sample.size(-1)    # Minibatch size - cardinality of distributions
d_hidden_size = 20   # Discriminator complexity
d_output_size = d_sample.size(-1)     # Single dimension for 'real' vs. 'fake' classification
d_n_layer = 2
# minibatch_size = d_input_size

d_learning_rate = 1e-2
g_learning_rate = 1e-2
# sgd_momentum = 0.9

num_epochs = 100
d_steps = 10
g_steps = 1

# dfe, dre, ge = 0, 0, 0
# d_real_data, d_fake_data, g_fake_data = None, None, None

# discriminator_activation_function = torch.sigmoid
# generator_activation_function = torch.tanh

G = Generator(input_size=g_input_size,
              hidden_size=g_hidden_size,
              n_layer = g_n_layer,
              output_size=g_output_size).cuda()
              #f=generator_activation_function)
D = Discriminator(input_size=d_input_size,
                  hidden_size=d_hidden_size,
                  n_layer = d_n_layer,
                  output_size=d_output_size).cuda()
                  #f=discriminator_activation_function)
criterion = nn.BCELoss()  # Binary cross entropy: http://pytorch.org/docs/nn.html#bceloss
opt_D = optim.RMSprop(D.parameters(), lr=d_learning_rate)
opt_G = optim.RMSprop(G.parameters(), lr=g_learning_rate)

for epoch in range(num_epochs):
    for d_index in range(d_steps):
        # 1. Train D on real+fake
        opt_D.zero_grad()

        #  1A: Train D on real
        D_real = D(d_sample)
        #  1B: Train D on fake
        G_fake = G(g_sample)
        D_fake = D(G_fake)
        D_loss = - torch.mean(torch.log(D_real.view(-1)) + torch.log(1. - D_fake.view(-1))) 
        D_loss.backward(retain_graph=True) # compute/store gradients
        opt_D.step() # Only optimizes D's parameters; changes based on stored gradients from backward()

    for g_index in range(g_steps):
        # 2. Train G on D's response (but DO NOT train D on these labels)
        opt_G.zero_grad()

        G_fake = G(g_sample)
        D_fake = D(G_fake)
        G_loss = torch.mean(torch.log(1. - D_fake.view(-1)))

        G_loss.backward()
        opt_G.step() # Only optimizes G's parameters
    
#     G_fake = G(g_sample)
#     D_real = D(d_sample)
#     D_fake = D(G_fake)

#     D_loss = - torch.mean(torch.log(D_real.view(-1)) + torch.log(1. - D_fake.view(-1)))
#     G_loss = torch.mean(torch.log(1. - D_fake.view(-1)))

#     D_optimizer.zero_grad()
#     D_loss.backward(retain_graph=True)
#     torch.nn.utils.clip_grad_norm(D.parameters(), 1)
#     D_optimizer.step()

#     G_optimizer.zero_grad()
#     G_loss.backward()
#     torch.nn.utils.clip_grad_norm(G.parameters(), 1)
#     G_optimizer.step()
    
    print("D: "+str(D_loss))
    print("G: "+str(G_loss))


In [0]:
#@title print results
print(D_real[0:3,0,0])
print(D_fake[0:3,0,0])
print(D_loss)
print(G_loss)
print(d_sample[0:10,0,0])
print(G_fake[0:10,0,0])

tensor([0.4871, 0.2817, 0.5049], device='cuda:0', grad_fn=<SelectBackward>)
tensor([0.3819, 0.3730, 0.3817], device='cuda:0', grad_fn=<SelectBackward>)
tensor(1.3820, device='cuda:0', grad_fn=<NegBackward>)
tensor(-0.6869, device='cuda:0', grad_fn=<MeanBackward0>)
tensor([ 0.3149, -0.2786,  0.3910,  0.1023, -0.0827, -0.0647,  0.0127, -0.3739,
        -0.2918, -0.0942], device='cuda:0')
tensor([ 0.0156, -0.0239,  0.0148, -0.0010, -0.0193, -0.0025,  0.0016, -0.0216,
        -0.0223, -0.0163], device='cuda:0', grad_fn=<SelectBackward>)


In [0]:
#@title show results
result = G(g_sample).cpu()
result = result.data.numpy() 
result = np.array(result).flatten()
librosa.output.write_wav('result_v3.wav',result,src)
ipd.Audio('result_v3.wav')

In [0]:
#@title save G
# save
torch.save(G.state_dict(), "G.pt")

In [0]:
#@title load G
# load
model = Generator(input_size=g_input_size,
              hidden_size=g_hidden_size,
              n_layer = g_n_layer,
              output_size=g_output_size).cuda()
model.load_state_dict(torch.load("G.pt"))
# model.eval()

In [0]:
#@title test on other samples
y1, sr1 = librosa.load('Money.mp3', mono=True,duration = 10)
test1_sample = np.array(y1)
print(y1)
time_steps = 500

music_length = len(y1)
sequence_size = int(music_length/time_steps)

test1_sample = np.zeros((sequence_size,time_steps))
for i in range(sequence_size):
    test1_sample[i] = y1[time_steps*i:time_steps*(i+1)]
  
test1_sample = test1_sample.reshape(sequence_size,time_steps,1)
test1_sample = Variable(torch.tensor(test1_sample)).float().cuda()

result = model(test1_sample).cpu()
result = result.data.numpy() 
result = np.array(result).flatten()
librosa.output.write_wav('result_v3.wav',result,src)
ipd.Audio('result_v3.wav')

[-0.12442017  0.02102661 -0.13696289 ... -0.03295898 -0.05911255
  0.02194214]


# **CNN GAN (unmodified)**

In [0]:
from __future__ import print_function
import argparse
import os
import random
import torch
import torch.nn as nn
import torch.nn.parallel
import torch.backends.cudnn as cudnn
import torch.optim as optim
import torch.utils.data
import torchvision.datasets as dset
import torchvision.transforms as transforms
import torchvision.utils as vutils


parser = argparse.ArgumentParser()
parser.add_argument('--dataset', required=True, help='cifar10 | lsun | mnist |imagenet | folder | lfw | fake')
parser.add_argument('--dataroot', required=True, help='path to dataset')
parser.add_argument('--workers', type=int, help='number of data loading workers', default=2)
parser.add_argument('--batchSize', type=int, default=64, help='input batch size')
parser.add_argument('--imageSize', type=int, default=64, help='the height / width of the input image to network')
parser.add_argument('--nz', type=int, default=100, help='size of the latent z vector')
parser.add_argument('--ngf', type=int, default=64)
parser.add_argument('--ndf', type=int, default=64)
parser.add_argument('--niter', type=int, default=25, help='number of epochs to train for')
parser.add_argument('--lr', type=float, default=0.0002, help='learning rate, default=0.0002')
parser.add_argument('--beta1', type=float, default=0.5, help='beta1 for adam. default=0.5')
parser.add_argument('--cuda', action='store_true', help='enables cuda')
parser.add_argument('--ngpu', type=int, default=1, help='number of GPUs to use')
parser.add_argument('--netG', default='', help="path to netG (to continue training)")
parser.add_argument('--netD', default='', help="path to netD (to continue training)")
parser.add_argument('--outf', default='.', help='folder to output images and model checkpoints')
parser.add_argument('--manualSeed', type=int, help='manual seed')

opt = parser.parse_args()
print(opt)

try:
    os.makedirs(opt.outf)
except OSError:
    pass

if opt.manualSeed is None:
    opt.manualSeed = random.randint(1, 10000)
print("Random Seed: ", opt.manualSeed)
random.seed(opt.manualSeed)
torch.manual_seed(opt.manualSeed)

cudnn.benchmark = True

if torch.cuda.is_available() and not opt.cuda:
    print("WARNING: You have a CUDA device, so you should probably run with --cuda")

if opt.dataset in ['imagenet', 'folder', 'lfw']:
    # folder dataset
    dataset = dset.ImageFolder(root=opt.dataroot,
                               transform=transforms.Compose([
                                   transforms.Resize(opt.imageSize),
                                   transforms.CenterCrop(opt.imageSize),
                                   transforms.ToTensor(),
                                   transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),
                               ]))
    nc=3
elif opt.dataset == 'lsun':
    dataset = dset.LSUN(root=opt.dataroot, classes=['bedroom_train'],
                        transform=transforms.Compose([
                            transforms.Resize(opt.imageSize),
                            transforms.CenterCrop(opt.imageSize),
                            transforms.ToTensor(),
                            transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),
                        ]))
    nc=3
elif opt.dataset == 'cifar10':
    dataset = dset.CIFAR10(root=opt.dataroot, download=True,
                           transform=transforms.Compose([
                               transforms.Resize(opt.imageSize),
                               transforms.ToTensor(),
                               transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),
                           ]))
    nc=3

elif opt.dataset == 'mnist':
        dataset = dset.MNIST(root=opt.dataroot, download=True,
                           transform=transforms.Compose([
                               transforms.Resize(opt.imageSize),
                               transforms.ToTensor(),
                               transforms.Normalize((0.5,), (0.5,)),
                           ]))
        nc=1

elif opt.dataset == 'fake':
    dataset = dset.FakeData(image_size=(3, opt.imageSize, opt.imageSize),
                            transform=transforms.ToTensor())
    nc=3

assert dataset
dataloader = torch.utils.data.DataLoader(dataset, batch_size=opt.batchSize,
                                         shuffle=True, num_workers=int(opt.workers))

device = torch.device("cuda:0" if opt.cuda else "cpu")
ngpu = int(opt.ngpu)
nz = int(opt.nz)
ngf = int(opt.ngf)
ndf = int(opt.ndf)


# custom weights initialization called on netG and netD
def weights_init(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        m.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        m.weight.data.normal_(1.0, 0.02)
        m.bias.data.fill_(0)


class Generator(nn.Module):
    def __init__(self, ngpu):
        super(Generator, self).__init__()
        self.ngpu = ngpu
        self.main = nn.Sequential(
            # input is Z, going into a convolution
            nn.ConvTranspose2d(     nz, ngf * 8, 4, 1, 0, bias=False),
            nn.BatchNorm2d(ngf * 8),
            nn.ReLU(True),
            # state size. (ngf*8) x 4 x 4
            nn.ConvTranspose2d(ngf * 8, ngf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 4),
            nn.ReLU(True),
            # state size. (ngf*4) x 8 x 8
            nn.ConvTranspose2d(ngf * 4, ngf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 2),
            nn.ReLU(True),
            # state size. (ngf*2) x 16 x 16
            nn.ConvTranspose2d(ngf * 2,     ngf, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf),
            nn.ReLU(True),
            # state size. (ngf) x 32 x 32
            nn.ConvTranspose2d(    ngf,      nc, 4, 2, 1, bias=False),
            nn.Tanh()
            # state size. (nc) x 64 x 64
        )

    def forward(self, input):
        if input.is_cuda and self.ngpu > 1:
            output = nn.parallel.data_parallel(self.main, input, range(self.ngpu))
        else:
            output = self.main(input)
        return output


netG = Generator(ngpu).to(device)
netG.apply(weights_init)
if opt.netG != '':
    netG.load_state_dict(torch.load(opt.netG))
print(netG)


class Discriminator(nn.Module):
    def __init__(self, ngpu):
        super(Discriminator, self).__init__()
        self.ngpu = ngpu
        self.main = nn.Sequential(
            # input is (nc) x 64 x 64
            nn.Conv2d(nc, ndf, 4, 2, 1, bias=False),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf) x 32 x 32
            nn.Conv2d(ndf, ndf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 2),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*2) x 16 x 16
            nn.Conv2d(ndf * 2, ndf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 4),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*4) x 8 x 8
            nn.Conv2d(ndf * 4, ndf * 8, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 8),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*8) x 4 x 4
            nn.Conv2d(ndf * 8, 1, 4, 1, 0, bias=False),
            nn.Sigmoid()
        )

    def forward(self, input):
        if input.is_cuda and self.ngpu > 1:
            output = nn.parallel.data_parallel(self.main, input, range(self.ngpu))
        else:
            output = self.main(input)

        return output.view(-1, 1).squeeze(1)


netD = Discriminator(ngpu).to(device)
netD.apply(weights_init)
if opt.netD != '':
    netD.load_state_dict(torch.load(opt.netD))
print(netD)

criterion = nn.BCELoss()

fixed_noise = torch.randn(opt.batchSize, nz, 1, 1, device=device)
real_label = 1
fake_label = 0

# setup optimizer
optimizerD = optim.Adam(netD.parameters(), lr=opt.lr, betas=(opt.beta1, 0.999))
optimizerG = optim.Adam(netG.parameters(), lr=opt.lr, betas=(opt.beta1, 0.999))

for epoch in range(opt.niter):
    for i, data in enumerate(dataloader, 0):
        ############################
        # (1) Update D network: maximize log(D(x)) + log(1 - D(G(z)))
        ###########################
        # train with real
        netD.zero_grad()
        real_cpu = data[0].to(device)
        batch_size = real_cpu.size(0)
        label = torch.full((batch_size,), real_label, device=device)

        output = netD(real_cpu)
        errD_real = criterion(output, label)
        errD_real.backward()
        D_x = output.mean().item()

        # train with fake
        noise = torch.randn(batch_size, nz, 1, 1, device=device)
        fake = netG(noise)
        label.fill_(fake_label)
        output = netD(fake.detach())
        errD_fake = criterion(output, label)
        errD_fake.backward()
        D_G_z1 = output.mean().item()
        errD = errD_real + errD_fake
        optimizerD.step()

        ############################
        # (2) Update G network: maximize log(D(G(z)))
        ###########################
        netG.zero_grad()
        label.fill_(real_label)  # fake labels are real for generator cost
        output = netD(fake)
        errG = criterion(output, label)
        errG.backward()
        D_G_z2 = output.mean().item()
        optimizerG.step()

        print('[%d/%d][%d/%d] Loss_D: %.4f Loss_G: %.4f D(x): %.4f D(G(z)): %.4f / %.4f'
              % (epoch, opt.niter, i, len(dataloader),
                 errD.item(), errG.item(), D_x, D_G_z1, D_G_z2))
        if i % 100 == 0:
            vutils.save_image(real_cpu,
                    '%s/real_samples.png' % opt.outf,
                    normalize=True)
            fake = netG(fixed_noise)
            vutils.save_image(fake.detach(),
                    '%s/fake_samples_epoch_%03d.png' % (opt.outf, epoch),
                    normalize=True)

    # do checkpointing
    torch.save(netG.state_dict(), '%s/netG_epoch_%d.pth' % (opt.outf, epoch))
    torch.save(netD.state_dict(), '%s/netD_epoch_%d.pth' % (opt.outf, epoch))

# **sample GAN code (unmodified)**

In [0]:
# https://github.com/devnag/pytorch-generative-adversarial-networks/blob/master/gan_pytorch.py

# import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable

# ##### DATA: Target data and generator input data

d_sampler = torch.Tensor(d_sample)
gi_sampler = torch.Tensor(g_sample)

# ##### MODELS: Generator model and discriminator model

class Generator(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, f):
        super(Generator, self).__init__()
        self.map1 = nn.Linear(input_size, hidden_size)
        self.map2 = nn.Linear(hidden_size, hidden_size)
        self.map3 = nn.Linear(hidden_size, output_size)
        self.f = f

    def forward(self, x):
        x = self.map1(x)
        x = self.f(x)
        x = self.map2(x)
        x = self.f(x)
        x = self.map3(x)
        return x

class Discriminator(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, f):
        super(Discriminator, self).__init__()
        self.map1 = nn.Linear(input_size, hidden_size)
        self.map2 = nn.Linear(hidden_size, hidden_size)
        self.map3 = nn.Linear(hidden_size, output_size)
        self.f = f

    def forward(self, x):
        x = self.f(self.map1(x))
        x = self.f(self.map2(x))
        return self.f(self.map3(x))

# Model parameters
g_input_size =  len(yc)     # Random noise dimension coming into generator, per output vector
g_hidden_size = 100     # Generator complexity
g_output_size = len(yc)     # Size of generated output vector
d_input_size = len(y)    # Minibatch size - cardinality of distributions
d_hidden_size = 10    # Discriminator complexity
d_output_size = len(y)     # Single dimension for 'real' vs. 'fake' classification
minibatch_size = d_input_size

d_learning_rate = 1e-2
g_learning_rate = 1e-2
sgd_momentum = 0.9

num_epochs = 5
d_steps = 10
g_steps = 10

dfe, dre, ge = 0, 0, 0
d_real_data, d_fake_data, g_fake_data = None, None, None

discriminator_activation_function = torch.sigmoid
generator_activation_function = torch.tanh

G = Generator(input_size=g_input_size,
              hidden_size=g_hidden_size,
              output_size=g_output_size,
              f=generator_activation_function)
D = Discriminator(input_size=d_input_size,
                  hidden_size=d_hidden_size,
                  output_size=d_output_size,
                  f=discriminator_activation_function)
criterion = nn.BCELoss()  # Binary cross entropy: http://pytorch.org/docs/nn.html#bceloss
d_optimizer = optim.SGD(D.parameters(), lr=d_learning_rate, momentum=sgd_momentum)
g_optimizer = optim.SGD(G.parameters(), lr=g_learning_rate, momentum=sgd_momentum)

for epoch in range(num_epochs):
    for d_index in range(d_steps):
        # 1. Train D on real+fake
        D.zero_grad()

        #  1A: Train D on real
        d_real_data = Variable(d_sampler(d_input_size))
        d_real_decision = D(preprocess(d_real_data))
        d_real_error = criterion(d_real_decision, Variable(torch.ones([1,1])))  # ones = true
        d_real_error.backward() # compute/store gradients, but don't change params

        #  1B: Train D on fake
        d_gen_input = Variable(gi_sampler(minibatch_size, g_input_size))
        d_fake_data = G(d_gen_input).detach()  # detach to avoid training G on these labels
        d_fake_decision = D(preprocess(d_fake_data.t()))
        d_fake_error = criterion(d_fake_decision, Variable(torch.zeros([1,1])))  # zeros = fake
        d_fake_error.backward()
        d_optimizer.step()     # Only optimizes D's parameters; changes based on stored gradients from backward()

    for g_index in range(g_steps):
        # 2. Train G on D's response (but DO NOT train D on these labels)
        G.zero_grad()

        gen_input = Variable(gi_sampler(minibatch_size, g_input_size))
        g_fake_data = G(gen_input)
        dg_fake_decision = D(preprocess(g_fake_data.t()))
        g_error = criterion(dg_fake_decision, Variable(torch.ones([1,1])))  # Train G to pretend it's genuine

        g_error.backward()
        g_optimizer.step()  # Only optimizes G's parameters

In [0]:
result = np.array(result).flatten()
librosa.output.write_wav('result.wav',result,sr)
ipd.Audio('result.wav')